In [35]:
# Import all necessary libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as pl
import seaborn as sn
import folium
import json
import geopandas as gpd
import branca.colormap as cm
from IPython.display import IFrame

In [2]:
#Import final, cleaned dataset
df = pd.read_csv('data/final.csv',encoding='cp1252')

In [6]:
#Create a groupby dataframe that gives us the mean in each numeric column for each state
state_averages = df.groupby(['State']).mean()

In [7]:
state_averages.head()

Unnamed: 0    District_ID           Zip  Zip_Population  \
State                                                              
AK     42368.300948  200365.277251  99657.786730    39081.149289   
AL     42265.726790  101751.307692  35877.150309    45956.251989   
AR     46821.170311  506829.497123  72309.643268    50772.945915   
AZ     31924.712526  403709.549281  85456.541581    96028.526181   
CA     30647.066999  621498.526266  93211.979367   121501.691569   

       Median_Income  Property_Taxes  Percent_Taxes  Per_Pupil_Spending  \
State                                                                     
AK      62940.789100   108671.718009      35.599052        13017.838863   
AL      65768.247569   131468.635721      35.251370        13323.150309   
AR      65707.849252   109583.352129      35.844534        13216.017261   
AZ      67320.849589   155278.840862      36.003183        13146.525154   
CA      65141.444682   141595.784774      34.521487        13250.342108   

       Per_Pupil_Support  Per_Pupil_Support_Staff  Per_Pupil_Salaries  \
State                                                                   
AK            783.959716               587.507109         4918.635071   
AL            817.709991               653.830239         4960.439434   
AR            745.814730               575.405063         5020.562716   
AZ            792.990760               641.340349         4904.075975   
CA            867.152615               689.597533         4849.451797   

       %_Proficient_Reading    Target  
State                                  
AK                36.357820  0.376777  
AL                42.304156  0.339523  
AR                42.326812  0.339471  
AZ                42.897331  0.405031  
CA                47.732717  0.469347

In [12]:
state_average_reading = state_averages[['%_Proficient_Reading']]

In [21]:
state_average_reading.shape

(43, 1)

Geojson file below courtesy of [Eric Celeste](https://eric.clst.org/tech/usgeojson/). 

In [9]:
#Load Geojson
with open('data/gz_2010_us_040_00_500k.json', 'r') as jsonSea:
    jsdata = json.load(jsonSea)
tmp = jsdata

In [17]:
# Read in  GeoJSON file as a Geopandas dataframe 
loc_data = gpd.read_file('data/gz_2010_us_040_00_500k.json')

GEO_ID STATE           NAME LSAD  CENSUSAREA  \
0  0400000US23    23          Maine        30842.923   
1  0400000US25    25  Massachusetts         7800.058   
2  0400000US26    26       Michigan        56538.901   
3  0400000US30    30        Montana       145545.801   
4  0400000US32    32         Nevada       109781.180   

                                            geometry  
0  MULTIPOLYGON (((-67.61976 44.51975, -67.61541 ...  
1  MULTIPOLYGON (((-70.83204 41.60650, -70.82373 ...  
2  MULTIPOLYGON (((-88.68443 48.11579, -88.67563 ...  
3  POLYGON ((-104.05770 44.99743, -104.25015 44.9...  
4  POLYGON ((-114.05060 37.00040, -114.04999 36.9...

In [18]:
loc_data.shape

(52, 6)

In [20]:
#All we need from the GeoJSON is the location data tied to state, so drop all other columns
geos = loc_data[['NAME' , 'geometry']]
geos.head()

NAME                                           geometry
0          Maine  MULTIPOLYGON (((-67.61976 44.51975, -67.61541 ...
1  Massachusetts  MULTIPOLYGON (((-70.83204 41.60650, -70.82373 ...
2       Michigan  MULTIPOLYGON (((-88.68443 48.11579, -88.67563 ...
3        Montana  POLYGON ((-104.05770 44.99743, -104.25015 44.9...
4         Nevada  POLYGON ((-114.05060 37.00040, -114.04999 36.9...

In [22]:
#Since reading achievement data uses abbreviations, need to match state geo data with abbreviations
abbrevs = pd.read_csv('data/state_abbrevs.csv')

In [26]:
geos = geos.merge(abbrevs, left_on='NAME', right_on='State', how='inner')

In [28]:
#Drop extra columsn
geos = geos[['Code','geometry']]

In [29]:
state_average_reading

%_Proficient_Reading
State                      
AK                36.357820
AL                42.304156
AR                42.326812
AZ                42.897331
CA                47.732717
CO                44.331698
CT                56.829883
DC                32.429319
DE                47.641618
FL                52.739091
GA                41.496735
HI                52.432331
ID                50.762360
IL                34.593998
IN                47.192674
KS                35.676548
KY                51.464439
LA                68.387590
MA                52.507535
MD                43.409455
ME                53.467647
MI                45.249543
MO                46.289995
MS                39.017442
NC                43.591125
NE                50.091036
NH                54.526523
NJ                56.160329
NM                30.806597
NV                45.537829
NY                54.650847
OH                61.760336
OK                31.548409
OR                52.157522
PA                61.588719
RI                43.158491
SC                47.786417
TN                32.830421
TX                45.066777
UT                44.872340
VA                75.946541
WA                58.532468
WY                53.111913

In [33]:
#Now merge with reading data
map_df = geos.merge(state_average_reading, left_on='Code', right_index=True,how='inner')

In [34]:
map_df

Code                                           geometry  \
0    ME  MULTIPOLYGON (((-67.61976 44.51975, -67.61541 ...   
1    MA  MULTIPOLYGON (((-70.83204 41.60650, -70.82373 ...   
2    MI  MULTIPOLYGON (((-88.68443 48.11579, -88.67563 ...   
4    NV  POLYGON ((-114.05060 37.00040, -114.04999 36.9...   
5    NJ  POLYGON ((-75.52684 39.65571, -75.52634 39.656...   
6    NY  MULTIPOLYGON (((-71.94356 41.28668, -71.92680 ...   
7    NC  MULTIPOLYGON (((-82.60288 36.03983, -82.60074 ...   
8    OH  MULTIPOLYGON (((-82.81349 41.72347, -82.81049 ...   
9    PA  POLYGON ((-75.41504 39.80179, -75.42804 39.809...   
10   RI  MULTIPOLYGON (((-71.28157 41.64821, -71.27817 ...   
11   TN  POLYGON ((-81.67754 36.58812, -81.68014 36.585...   
12   TX  MULTIPOLYGON (((-97.13436 27.89633, -97.13360 ...   
13   UT  POLYGON ((-114.05060 37.00040, -114.05175 37.0...   
14   WA  MULTIPOLYGON (((-123.09055 49.00198, -123.0353...   
16   MD  MULTIPOLYGON (((-76.07147 38.20350, -76.04879 ...   
17   AL  MULTIPOLYGON (((-85.00237 31.00068, -85.02411 ...   
18   AK  MULTIPOLYGON (((-164.97620 54.13459, -164.9377...   
19   AZ  POLYGON ((-109.04522 36.99908, -109.04524 36.9...   
20   AR  POLYGON ((-94.55929 36.49950, -94.51948 36.499...   
21   CA  MULTIPOLYGON (((-122.44632 37.86105, -122.4385...   
22   CO  POLYGON ((-102.04224 36.99308, -102.05450 36.9...   
23   CT  MULTIPOLYGON (((-71.85957 41.32240, -71.86823 ...   
24   DE  MULTIPOLYGON (((-75.55945 39.62981, -75.55910 ...   
25   DC  POLYGON ((-77.03860 38.79151, -77.03890 38.800...   
26   FL  MULTIPOLYGON (((-85.15641 29.67963, -85.13740 ...   
27   GA  POLYGON ((-81.44412 30.70971, -81.44872 30.709...   
28   HI  MULTIPOLYGON (((-171.73761 25.79210, -171.7223...   
29   ID  POLYGON ((-111.04669 42.00157, -111.41587 42.0...   
30   IL  POLYGON ((-87.53233 39.99778, -87.53254 39.987...   
31   IN  POLYGON ((-88.02803 37.79922, -88.02938 37.803...   
33   KS  POLYGON ((-94.61808 36.99813, -94.62522 36.998...   
34   KY  MULTIPOLYGON (((-83.67541 36.60081, -83.67561 ...   
35   LA  MULTIPOLYGON (((-88.86507 29.75271, -88.88975 ...   
37   MS  MULTIPOLYGON (((-88.71072 30.25080, -88.65680 ...   
38   MO  POLYGON ((-89.53910 36.49820, -89.53452 36.491...   
39   NE  POLYGON ((-95.76565 40.58521, -95.76853 40.583...   
40   NH  MULTIPOLYGON (((-72.45852 42.72685, -72.45849 ...   
41   NM  POLYGON ((-109.05004 31.33250, -109.05017 31.4...   
43   OK  POLYGON ((-94.61792 36.49941, -94.61531 36.484...   
44   OR  POLYGON ((-117.22007 44.30138, -117.22245 44.2...   
45   SC  POLYGON ((-78.54109 33.85111, -78.55394 33.847...   
48   VA  MULTIPOLYGON (((-76.04653 37.95359, -76.04169 ...   
50   WY  POLYGON ((-109.05008 41.00066, -109.17368 41.0...   

    %_Proficient_Reading  
0              53.467647  
1              52.507535  
2              45.249543  
4              45.537829  
5              56.160329  
6              54.650847  
7              43.591125  
8              61.760336  
9              61.588719  
10             43.158491  
11             32.830421  
12             45.066777  
13             44.872340  
14             58.532468  
16             43.409455  
17             42.304156  
18             36.357820  
19             42.897331  
20             42.326812  
21             47.732717  
22             44.331698  
23             56.829883  
24             47.641618  
25             32.429319  
26             52.739091  
27             41.496735  
28             52.432331  
29             50.762360  
30             34.593998  
31             47.192674  
33             35.676548  
34             51.464439  
35             68.387590  
37             39.017442  
38             46.289995  
39             50.091036  
40             54.526523  
41             30.806597  
43             31.548409  
44             52.157522  
45             47.786417  
48             75.946541  
50             53.111913

In [36]:
#Visualize each state's average readign proficiency on a map 

# Initiate folium map 
US_reading = folium.Map(location=[48, -102], zoom_start=3)

# Change map to grayed-out version 
folium.TileLayer('CartoDB positron',name="Light Map",control=False).add_to(US_reading)

# Create colormap 
colormap = cm.linear.YlGnBu_09.to_step(data=map_df['%_Proficient_Reading'], method='quant', quantiles=[0,0.2,0.4,0.6,0.8,1])
colormap

# Creating a choropleth map 
folium.Choropleth(
            geo_data = map_df,
            fill_opacity = 0.7,
            line_opacity = 0.2,
            data = map_df,
            #refers to which key within json file to map zip to
            key_on = 'feature.properties.Code',
            # first element is location, second element is reading proficiency
            columns = ['Code', '%_Proficient_Reading'],
            # change the colormap to whatever you want
            fill_color = 'YlGnBu',
            legend_name = 'Price'
).add_to(US_reading)

style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}

NIL = folium.features.GeoJson(
    data = map_df,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    tooltip=folium.features.GeoJsonTooltip(
        fields=['Code', '%_Proficient_Reading'],
        aliases=['State Name', 'Percent of Public School Students Proficient in Reading'],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)
US_reading.add_child(NIL)
US_reading.keep_in_front(NIL)

folium.LayerControl().add_to(US_reading)
US_reading.save('data/us_reading_map.html')

US_reading

In [37]:
IFrame(src='data/US_reading_map.html', width=950, height=600)